In [1]:
import folium
import geopandas as gpd
from folium import Choropleth, GeoJson
from folium import FeatureGroup

In [2]:
parroquias = gpd.read_file('C:/Users/Usuario/OneDrive - Universidad Técnica Particular de Loja - UTPL/Courser/ecolideres/canton_un.shp') 

In [28]:
import pandas as pd
plants = pd.read_csv('C:/Users/Usuario/OneDrive - Universidad Técnica Particular de Loja - UTPL/Courser/ecolideres/arboles.txt', delimiter=';')

In [29]:
print(plants.head())

   FID  OBJECTID       Fecha  Codigo   Especie  Altura              POINT_X  \
0    0         1  2022-05-21      93  Guayacán       0  -79,221422000299995   
1    1         2  2022-05-21     163  Guayacán       0  -79,221543999700003   
2    2         3  2022-05-21     205  Guayacán       0  -79,221702999800002   
3    3         4  2022-05-21     180  Guayacán       0  -79,221698999599994   
4    4         5  2022-05-21      85  Guayacán       0  -79,221682999799995   

              POINT_Y  
0  -3,959095999580000  
1  -3,959809000090000  
2  -3,960421000430000  
3  -3,960510000040000  
4  -3,961426000010000  


In [30]:
plants['POINT_X'] = plants['POINT_X'].str.replace(',', '.').astype(float)
plants['POINT_Y'] = plants['POINT_Y'].str.replace(',', '.').astype(float)

In [31]:
MyMap = folium.Map(location=[plants['POINT_Y'].mean(), plants['POINT_X'].mean()], zoom_start=9)

In [32]:
folium.TileLayer('Esri.WorldImagery', name='Mapa Satelital').add_to(MyMap)

In [33]:
folium.GeoJson(
    parroquias,
    name='Límites parroquiales',
    style_function=lambda feature: {
        'color': 'black',
        'weight': 2,
        'fillOpacity': 0.1,
    }
).add_to(MyMap)

In [34]:
bounds = [[plants['POINT_Y'].min(), plants['POINT_X'].min()],
          [plants['POINT_Y'].max(), plants['POINT_X'].max()]]

MyMap.fit_bounds(bounds)

In [ ]:
colors = [
    'DarkOrange',  'DeepSkyBlue', 
    'DodgerBlue', 'Firebrick', 'FloralWhite', 'ForestGreen', 'Gainsboro',
    'LightSeaGreen', 'LightSkyBlue', 'LightSlateGray', 'LightSteelBlue', 'LightYellow',
    'MediumBlue', 'MediumForestGreen', 'MediumPurple',
    'OliveDrab', 'Orange', 'Orchid', 'PaleGoldenrod', 'PaleGreen',
    'PowderBlue', 'RosyBrown', 'RoyalBlue', 'SandyBrown', 'SeaShell',
    'Tan', 'Thistle', 'Tomato', 'Turquoise', 'Violet',
    'Wheat', 'YellowGreen', 
    'CadetBlue', 'Burlywood'
]


species = plants['Especie'].unique()
color_map = {species[i]: colors[i % len(colors)] for i in range(len(species))}

In [51]:
for especie in species:
    specie_data = plants[plants['Especie'] == especie]

    marker_layer = FeatureGroup(name=especie)

    for idx, row in specie_data.iterrows():
        if pd.notnull(row['POINT_Y']) and pd.notnull(row['POINT_X']):
            folium.CircleMarker(
                location=[row['POINT_Y'], row['POINT_X']],
                radius=7,  # Ajusta el tamaño del marcador
                color=color_map.get(especie, 'blue'),  # Contorno del marcador
                fill=True,
                fill_color=color_map.get(especie, 'blue'),  # Color de relleno
                fill_opacity=0.7,
                popup=folium.Popup(f"""
                    <div style="font-size: 14px;">
                        <b>Planta:</b> {row['Especie']}<br>
                        <b>Fecha:</b> {row['Fecha']}<br>
                        <b>Código:</b> {row['Codigo']}<br>
                        <b>Altura cm:</b> {row['Altura']}<br>
                    </div>
                """, max_width=300)
            ).add_to(marker_layer)

    marker_layer.add_to(MyMap)

In [52]:
folium.LayerControl().add_to(MyMap)

In [53]:
MyMap

In [40]:
# Título del mapa (opcional)
reforestacion_html = '''
<div style="position: absolute; top: 12px; left: 50px; background-color: rgba(255, 255, 255, 0.9); 
    border: 2px solid black; padding: 5px; border-radius: 5px; z-index: 1000;">
    <h2 style="font-weight: bold; margin: 0;">Locación de especies sembradas</h2>
</div>
'''
MyMap.get_root().html.add_child(folium.Element(reforestacion_html))

In [41]:
MyMap

In [43]:
MyMap.save('C:/Users/Usuario/OneDrive - Universidad Técnica Particular de Loja - UTPL/Courser/ecolideres/reforestacion.html')